# A Coronavirus Dashboard for Croatia
This [Jupyter Notebook](https://jupyter.org/) gives an overview of reported [SARS-CoV-2](https://en.wikipedia.org/wiki/Severe_acute_respiratory_syndrome_coronavirus_2) infections in Croatia. It uses historic data from [koronavirus.hr](https://koronavirus.hr) to provide a breakdown for each of the [counties of Croatia](https://en.wikipedia.org/wiki/Counties_of_Croatia). The data used here can also be found in our [GitHub Repository](https://github.com/saraedum/koronavirus-hr). If you spot a mistake, please create an [issue](https://github.com/saraedum/koronavirus-hr/issues) or a [pull request](https://github.com/saraedum/koronavirus-hr/pulls).

> Disclaimer: The author has no background in Statistics or Epidemiology so there might be errors in data and presentation.

In [1]:
import pandas as pd

# We are scraping koronavirus.hr to get the total number of reported infections
# for each county and store them as a CSV file.
totals = pd.read_csv("koronavirus.csv", parse_dates=["timestamp"], index_col="timestamp")
totals['Croatia'] = totals.sum(axis=1)

# To make these number comparable, we put them in relation with the inhabitants of each county
# as recorded on Wikipedia.
inhabitants = {
 'Bjelovar-Bilogora':     119764,
 'Brod-Posavina':         158575,
 'Dubrovnik-Neretva':     122568,
 'City of Zagreb':        790017,
 'Istria':                208055,
 'Karlovac':              128899,
 'Koprivnica-Križevci':   115584,
 'Krapina-Zagorje':       132892,
 'Lika-Senj':              50927,
 'Međimurje':             113804,
 'Osijek-Baranja':        305032,
 'Požega-Slavonia':        78034,
 'Primorje-Gorski Kotar': 296195,
 'Šibenik-Knin':          109375,
 'Sisak-Moslavina':       172439,
 'Split-Dalmatia':        454798,
 'Varaždin':              175951,
 'Virovitica-Podravina':   84836,
 'Vukovar-Syrmia':        179521,
 'Zadar':                 170017,
 'Zagreb County':         317606,
}
inhabitants['Croatia'] = sum(inhabitants.values())
inhabitants = pd.DataFrame(inhabitants.values(), index=inhabitants.keys(), columns=["inhabitants"])

# The number of reported infections per 100000 inhabitants.
adjusted = totals.div(inhabitants["inhabitants"]/100000, axis='columns')

# The number of newly reported infections per 100000 inhabitants on that day.
diffs = adjusted.diff()

# The number of newly reported infections per 100000 inhabitants in the last 7 days (this is the measure typically used e.g. in Germany.)
weekly = diffs.rolling('7d').sum()

# The number of newly reported infections per 100000 inhabitants in the last 7 days (this is the measure typically used e.g. in the UK.)
fortnight = diffs.rolling('14d').sum()

# The weekly reproduction factor as used by https://pavelmayer.de/covid/risks/
rwk = (weekly + 5) / (fortnight - weekly + 5)

## Accumulated Reported Infections
The total reported infections in each of the counties of Croatia.

Note that you can double-click on a county name to only show that county.

In [2]:
import plotly.express as px
import plotly.graph_objects as go
pd.options.plotting.backend = "plotly"
focus = lambda plot: plot.update_traces({"visible":"legendonly"}).update_traces({"visible":True}, line={"color": "black"}, selector={"name":"Croatia"})

px.area(totals.drop(['Croatia'], axis=1)).update_layout(height=800)

## Daily Reported Infections per 100,000 Inhabitants
The reported infections in each county per day. To make these numbers comparable between counties, they are normalized to 100,000 inhabitants. For example a value of 10 in a county with 300,000 inhabitants means that 30 infections have been reported on that day.

Note that you can click on a county name to display data for that county.

There are some errors in the data for Zagreb in April and for Požega-Slavonia in September which lead to negative values in this chart.

In [3]:
focus(px.line(diffs).update_layout(height=800))

## Accumulated Reported Infections in a 7 Day Period per 100,000 Inhabitants
The German Robert Koch Institute uses this as an indicator on whether to propose a travel warning for regions of Croatia. Among other criteria, such a warning is typically issued when this value rises above 50.

Note that you can double-click on a county's name to only show that county.

In [4]:
focus(px.line(weekly).update_layout(height=800))

## $\mathrm{log}_2$ of the Weekly Reproduction Factor
The Weekly Reproduction Factor compares the reported infection of the last seven days with the reported infections of the 7 days before that. Here we show a log of a [modified quotient](https://pavelmayer.de/covid/risks/) of these two numbers. The values convey an idea of whether reported infections have been increasing in the past week or decreasing. Values below 0 indicate that the reported infections are decreasing, values above 0 indicate that the reported infections are increasing. For example a value of 1 roughly says that the past week reported twice as many infections than the week before that, whereas a value of -1 roughly says that the past week reported half as many infections than the week before that.

Note that you can double-click on a county's name to only show that county.

In [5]:
from math import log2
focus(px.line(rwk.applymap(lambda x: log2(x))).update_layout(height=800))

In [6]:
from IPython.display import display, Markdown, Latex
display(Markdown(f"""---
Last Update: {totals.index.max().date()}"""))

---
Last Update: 2022-02-26